# Satellite Plots

The code below provides an interactive dropdown menu to select a satellite.  
Upon selection, the corresponding plots of all six orbital elements for the chosen satellite will be displayed.  
This allows for easy visual exploration of each satellite's orbital behavior over time.


In [2]:
import pandas as pd
import plotly.graph_objects as go
import ipywidgets as widgets
from IPython.display import display

# List of orbital elements to plot
orbital_elements = ["eccentricity", "argument of perigee", "inclination", 
                    "mean anomaly", "Brouwer mean motion", "right ascension"]


# List of satellites
satellites = ["SARAL", "TOPEX", "CRYOSAT-2", "HAIYANG-2A", "JASON-1", "JASON-2", "JASON-3", 
              "SENTINEL-3A", "SENTINEL-3B", "SENTINEL-6A", 
              "FENGYUN-2D", "FENGYUN-2E", "FENGYUN-2H", "FENGYUN-2F", "FENGYUN-4A"]

# function to ensure timestamp column is UTC
# fengyun satellites has alreday utc so used convert() function to not crash.
def ensure_utc(series):
    if series.dt.tz is None:
        return series.dt.tz_localize('UTC')
    else:
        return series.dt.tz_convert('UTC')

# Function to load & preprocess satellite data
def load_satellite_data(satellite_name):
    file_path = f"/Users/kurinjiarivazhagan/Desktop/trimester 5/satellite_data/orbital_elements/{satellite_name}.csv"
    df = pd.read_csv(file_path)

    # Preprocessing Steps
    df.rename(columns={'Unnamed: 0': 'timestamp'}, inplace=True)
    df['timestamp'] = pd.to_datetime(df['timestamp']).dt.tz_localize('UTC')  
    df.set_index('timestamp', inplace=True)

    df['time_diff'] = df.index.to_series().diff()
    df['time_diff_days'] = df['time_diff'].dt.total_seconds() / 86400  

    return df

# Function to load & preprocess maneuver data
def load_maneuver_data(satellite_name):
    file_path = f"/Users/kurinjiarivazhagan/Desktop/trimester 5/satellite_data/orbital_elements/cleaned maneuver file/cleaned_{satellite_name}.csv"
    maneuver_df = pd.read_csv(file_path)

    # Preprocessing Maneuver Timestamps
    maneuver_df["Start_Timestamp"] = pd.to_datetime(maneuver_df["Start_Timestamp"])
    maneuver_df["End_Timestamp"] = pd.to_datetime(maneuver_df["End_Timestamp"])

    # function to make sure both columns are in UTC
    maneuver_df["Start_Timestamp"] = ensure_utc(maneuver_df["Start_Timestamp"])
    maneuver_df["End_Timestamp"] = ensure_utc(maneuver_df["End_Timestamp"])

    return maneuver_df

# Function to plot the selected satellite's data
def plot_satellite(selected_satellite):
    try:
        df = load_satellite_data(selected_satellite)
        maneuver_df = load_maneuver_data(selected_satellite)

        for element in orbital_elements:
            fig = go.Figure()
            fig.add_trace(go.Scatter(
                x=df.index, y=df[element], 
                mode="lines", name=element
            ))
            fig.add_trace(go.Scatter(
                x=[None],
                y=[None],
                mode='lines',
                line=dict(color="red", dash="dash"),
                name="Maneuver"
            ))
            for time in maneuver_df["Start_Timestamp"]:
                fig.add_shape(
                    type="line", 
                    x0=time, x1=time, 
                    y0=df[element].min(), y1=df[element].max(),
                    line=dict(color="red", width=1, dash="dash")  
                )

            fig.update_layout(
    title={
        'text': f"{element.title()} Over Time with Maneuvers for {selected_satellite}",
        'font': {'size': 25}
    },
    xaxis_title={
        'text': "Time (UTC)",
        'font': {'size': 25}
    },
    yaxis_title={
        'text': element.title(),
        'font': {'size': 25}
    },
    xaxis=dict(tickfont=dict(size=29)),
    yaxis=dict(tickfont=dict(size=29)),
    legend=dict(font=dict(size=21)),
    font=dict(size=20),  
    showlegend=True,
    template="plotly",
    width=1400,
    height=600
)



            fig.show()

    except Exception as e:
        print(f"Error loading or plotting {selected_satellite}: {e}")

# Dropdown widget for satellite selection
satellite_selector = widgets.Dropdown(
    options=satellites,
    description="Satellite:",
    style={'description_width': 'initial'}
)

# Button to trigger plotting
plot_button = widgets.Button(description="Plot Data")

# Function to handle button click
def on_button_click(b):
    plot_satellite(satellite_selector.value)

plot_button.on_click(on_button_click)

# Display 

display(satellite_selector, plot_button)



Dropdown(description='Satellite:', options=('SARAL', 'TOPEX', 'CRYOSAT-2', 'HAIYANG-2A', 'JASON-1', 'JASON-2',…

Button(description='Plot Data', style=ButtonStyle())

# Element Plot
The dropdown menu below allows selection of a specific orbital element.
Upon selection, the chosen element will be plotted for all 15 satellites.
This enables visual comparison of how that element evolves across different satellites, supporting the identification of patterns, anomalies, or inconsistencies.

In [1]:
import pandas as pd
import plotly.graph_objects as go
import ipywidgets as widgets
from IPython.display import display

# List of orbital elements to plot
orbital_elements = ["eccentricity", "argument of perigee", "inclination", 
                    "mean anomaly", "Brouwer mean motion", "right ascension"]

# List of satellites
satellites = ["SARAL", "TOPEX", "CRYOSAT-2", "HAIYANG-2A", "JASON-1", "JASON-2", "JASON-3", 
              "SENTINEL-3A", "SENTINEL-3B", "SENTINEL-6A", "FENGYUN-2D", "FENGYUN-2E", 
              "FENGYUN-2H", "FENGYUN-2F", "FENGYUN-4A"]

#function to safely ensure UTC timezone
def ensure_utc(series):
    if series.dt.tz is None:
        return series.dt.tz_localize('UTC')
    else:
        return series.dt.tz_convert('UTC')

# Load & preprocess satellite data
def load_satellite_data(satellite_name):
    file_path = f"/Users/kurinjiarivazhagan/Desktop/trimester 5/satellite_data/orbital_elements/{satellite_name}.csv"
    df = pd.read_csv(file_path)
    df.rename(columns={'Unnamed: 0': 'timestamp'}, inplace=True)
    df['timestamp'] = pd.to_datetime(df['timestamp']).dt.tz_localize('UTC')
    df.set_index('timestamp', inplace=True)
    df['time_diff'] = df.index.to_series().diff()
    df['time_diff_days'] = df['time_diff'].dt.total_seconds() / 86400
    return df

# Load & preprocess maneuver data
def load_maneuver_data(satellite_name):
    file_path = f"/Users/kurinjiarivazhagan/Desktop/trimester 5/satellite_data/orbital_elements/cleaned maneuver file/cleaned_{satellite_name}.csv"
    maneuver_df = pd.read_csv(file_path)
    maneuver_df["Start_Timestamp"] = ensure_utc(pd.to_datetime(maneuver_df["Start_Timestamp"]))
    maneuver_df["End_Timestamp"] = ensure_utc(pd.to_datetime(maneuver_df["End_Timestamp"]))
    return maneuver_df

# Plot the selected orbital element for all satellites
def plot_selected_element(selected_element):
    for satellite in satellites:
        try:
            df = load_satellite_data(satellite)
            maneuver_df = load_maneuver_data(satellite)

            if selected_element in df.columns:
                fig = go.Figure()

                # Plot the orbital element
                fig.add_trace(go.Scatter(
                    x=df.index, y=df[selected_element],
                    mode="lines", name=f"{selected_element} ({satellite})"
                ))
                fig.add_trace(go.Scatter(
                    x=[None], y=[None],
                    mode='lines',
                    line=dict(color="red", dash="dash"),
                    name="Maneuver"
                ))
                for time in maneuver_df["Start_Timestamp"]:
                    fig.add_shape(
                        type="line",
                        x0=time, x1=time,
                        y0=df[selected_element].min(), y1=df[selected_element].max(),
                        line=dict(color="red", width=1, dash="dash")
                    )
                fig.update_layout(
    title={
        'text': f"{selected_element.title()} Over Time for {satellite} (with Maneuvers)",
        'font': {'size': 25}
    },
    xaxis_title={
        'text': "Time (UTC)",
        'font': {'size': 25}
    },
    yaxis_title={
        'text': selected_element.title(),
        'font': {'size': 25}
    },
    xaxis=dict(tickfont=dict(size=22)),
    yaxis=dict(tickfont=dict(size=22)),
    legend=dict(font=dict(size=21)),
    font=dict(size=16),
    showlegend=True,
    template="plotly",
    width=1400,
    height=600
)



                fig.show()

            else:
                print(f"Element '{selected_element}' not found in {satellite}")

        except Exception as e:
            print(f"Error loading or plotting {satellite}: {e}")

# Dropdown widget for orbital element selection
element_selector = widgets.Dropdown(
    options=orbital_elements,
    description="Orbital Element:",
    style={'description_width': 'initial'}
)

# Button to trigger plotting
plot_button = widgets.Button(description="Plot Data")

def on_button_click(b):
    plot_selected_element(element_selector.value)

plot_button.on_click(on_button_click)

# Display 
display(element_selector, plot_button)


Dropdown(description='Orbital Element:', options=('eccentricity', 'argument of perigee', 'inclination', 'mean …

Button(description='Plot Data', style=ButtonStyle())